# Pré-processamento para o modelo
----

- Separação treino e teste
- Balanceamento do treino
- Normalização das variáveis numéricas
- Comportamento das variáveis em relação à variável de evasão

<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Importação-da-base-e-pacotes" data-toc-modified-id="Importação-da-base-e-pacotes-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Importação da base e pacotes</a></span><ul class="toc-item"><li><span><a href="#Variáveis-de-aluno-(L1)-e-escola-(L2):" data-toc-modified-id="Variáveis-de-aluno-(L1)-e-escola-(L2):-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Variáveis de aluno (L1) e escola (L2):</a></span></li></ul></li><li><span><a href="#Separação-treino-teste" data-toc-modified-id="Separação-treino-teste-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Separação treino-teste</a></span><ul class="toc-item"><li><span><a href="#Estratificada" data-toc-modified-id="Estratificada-2.1"><span class="toc-item-num">2.1&nbsp;&nbsp;</span>Estratificada</a></span></li><li><span><a href="#Aleatória-(balanceada)" data-toc-modified-id="Aleatória-(balanceada)-2.2"><span class="toc-item-num">2.2&nbsp;&nbsp;</span>Aleatória (balanceada)</a></span></li></ul></li><li><span><a href="#Nomalizando-variáveis-de-aluno" data-toc-modified-id="Nomalizando-variáveis-de-aluno-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Nomalizando variáveis de aluno</a></span><ul class="toc-item"><li><span><a href="#Normalizando-idade:-MixMax" data-toc-modified-id="Normalizando-idade:-MixMax-3.1"><span class="toc-item-num">3.1&nbsp;&nbsp;</span>Normalizando idade: MixMax</a></span></li></ul></li><li><span><a href="#Normalizando-variáveis-de-escola" data-toc-modified-id="Normalizando-variáveis-de-escola-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Normalizando variáveis de escola</a></span><ul class="toc-item"><li><span><a href="#Normalizando-numéricas:-Gaussiana" data-toc-modified-id="Normalizando-numéricas:-Gaussiana-4.1"><span class="toc-item-num">4.1&nbsp;&nbsp;</span>Normalizando numéricas: Gaussiana</a></span></li><li><span><a href="#Adicionando-as-indicadoras" data-toc-modified-id="Adicionando-as-indicadoras-4.2"><span class="toc-item-num">4.2&nbsp;&nbsp;</span>Adicionando as indicadoras</a></span></li></ul></li><li><span><a href="#Salvando-encoders" data-toc-modified-id="Salvando-encoders-5"><span class="toc-item-num">5&nbsp;&nbsp;</span>Salvando <em>encoders</em></a></span></li><li><span><a href="#Juntando-dados-normalizados-do-treino" data-toc-modified-id="Juntando-dados-normalizados-do-treino-6"><span class="toc-item-num">6&nbsp;&nbsp;</span>Juntando dados normalizados do treino</a></span></li><li><span><a href="#Normalizando-teste" data-toc-modified-id="Normalizando-teste-7"><span class="toc-item-num">7&nbsp;&nbsp;</span>Normalizando teste</a></span><ul class="toc-item"><li><span><a href="#Balanceamento" data-toc-modified-id="Balanceamento-7.1"><span class="toc-item-num">7.1&nbsp;&nbsp;</span>Balanceamento</a></span></li></ul></li></ul></div>

## Importação da base e pacotes

In [1]:
# dic_cor =  {0: "Não declarada",
#             1: "Branca",
#             2: "Preta",
#             3: "Parda",
#             4: "Amarela",
#             5: "Indígena"}

# dic_evasao = {0: 'Não evadiu', 1: 'Evadiu'}

# dic_regiao = {0: 'Rio (cidade)', 1: 'Grande Rio (região metropolitana)', 2: 'Outras regiões no estado'}

In [2]:
# %load first_cell.py
%reload_ext autoreload
%autoreload 2

from paths import RAW_PATH, TREAT_PATH, OUTPUT_PATH, FIGURES_PATH, MODEL_PATH

import os
from copy import deepcopy
import numpy as np
import pandas as pd
pd.options.display.max_columns = 999

import warnings
warnings.filterwarnings('ignore')

# Plotting
import plotly
import plotly.graph_objs as go
import cufflinks as cf
plotly.offline.init_notebook_mode(connected=True)

# Metrics
from plot_metrics import plot_roc, plot_confusion

cf.go_offline()
cf.set_config_file(offline=False, world_readable=True)

colorscale = ['#025951', '#8BD9CA', '#BF7F30', '#F2C124', '#8C470B', '#DFC27D']

In [3]:
df = pd.read_csv(TREAT_PATH / 'analysis' / 'df_clean.csv', index_col=0)

df = df.rename({'L2_INSE_VALOR_ABSOLUTO': 'L2_NU_INSE_VALOR', 
                'L2_INSE_NIVEL': 'L2_OR_INSE_NIVEL'}, axis=1)

df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 146214 entries, 112132289130 to 112980381895
Data columns (total 41 columns):
L1_NU_IDADE_REFERENCIA              146214 non-null int64
L1_IN_SEXO                          146214 non-null int64
L1_TP_COR_RACA                      146214 non-null int64
L1_IN_TRANSPORTE_PUBLICO            146214 non-null int64
L1_ID_TURMA                         146214 non-null int64
L2_CO_ENTIDADE                      146214 non-null int64
L1_IN_EVASAO                        146214 non-null int64
L1_IN_DISTORCAO                     146214 non-null int64
L1_IN_MUNICIPIO_NASC_RIO            146214 non-null int64
L1_IN_MUNICIPIO_NASC_MET            146214 non-null int64
L1_IN_MUNICIPIO_NASC_OUT            146214 non-null int64
L2_IN_MUNICIPIO_RIO                 146214 non-null int64
L2_IN_MUNICIPIO_MET                 146214 non-null int64
L2_IN_MUNICIPIO_OUT                 146214 non-null int64
L1_IN_DIF_MUN_ESCOLA_NASC           146214 non-null int64
L2

In [4]:
df.head(2)

L1_NU_IDADE_REFERENCIA  L1_IN_SEXO  L1_TP_COR_RACA  \
L1_ID                                                              
112132289130                      16           1               0   
113220290328                      20           1               0   

              L1_IN_TRANSPORTE_PUBLICO  L1_ID_TURMA  L2_CO_ENTIDADE  \
L1_ID                                                                 
112132289130                         0      6062013        33009627   
113220290328                         0      6062013        33009627   

              L1_IN_EVASAO  L1_IN_DISTORCAO  L1_IN_MUNICIPIO_NASC_RIO  \
L1_ID                                                                   
112132289130             0                0                         0   
113220290328             1                1                         0   

              L1_IN_MUNICIPIO_NASC_MET  L1_IN_MUNICIPIO_NASC_OUT  \
L1_ID                                                              
112132289130                         0                         1   
113220290328                         0                         1   

              L2_IN_MUNICIPIO_RIO  L2_IN_MUNICIPIO_MET  L2_IN_MUNICIPIO_OUT  \
L1_ID                                                                         
112132289130                    0                    0                    1   
113220290328                    0                    0                    1   

              L1_IN_DIF_MUN_ESCOLA_NASC  L2_IN_AGUA_CACIMBA  \
L1_ID                                                         
112132289130                          0                 0.0   
113220290328                          0                 0.0   

              L2_IN_LABORATORIO_CIENCIAS  L2_IN_QUADRA_ESPORTES_DESCOBERTA  \
L1_ID                                                                        
112132289130                         1.0                               0.0   
113220290328                         1.0                               0.0   

              L2_IN_BANHEIRO_FORA_PREDIO  L2_IN_AUDITORIO  L2_IN_ALOJAM_ALUNO  \
L1_ID                                                                           
112132289130                         1.0              1.0                 0.0   
113220290328                         1.0              1.0                 0.0   

              L2_IN_EQUIP_VIDEOCASSETE  L2_IN_EQUIP_PARABOLICA  \
L1_ID                                                            
112132289130                       0.0                     0.0   
113220290328                       0.0                     0.0   

              L2_IN_EQUIP_RETROPROJETOR  L2_IN_EQUIP_IMPRESSORA  \
L1_ID                                                             
112132289130                        1.0                     1.0   
113220290328                        1.0                     1.0   

              L2_IN_EQUIP_FAX  L2_NU_EQUIP_TV  L2_NU_EQUIP_DVD  \
L1_ID                                                            
112132289130              1.0             5.0              2.0   
113220290328              1.0             5.0              2.0   

              L2_NU_EQUIP_COPIADORA  L2_NU_EQUIP_SOM  L2_NU_EQUIP_MULTIMIDIA  \
L1_ID                                                                          
112132289130                    3.0              1.0                     6.0   
113220290328                    3.0              1.0                     6.0   

              L2_NU_EQUIP_FOTO  L2_NU_COMP_ALUNO  L2_NU_FUNCIONARIOS  \
L1_ID                                                                  
112132289130               1.0              72.0               228.0   
113220290328               1.0              72.0               228.0   

              L2_IN_EJA  L2_IN_COMUM_FUND_AF  L2_NU_INSE_VALOR  \
L1_ID                                                            
112132289130        0.0                  0.0             48.78   
113220290328        0.0                  0.0             48.78   

        

### Variáveis de aluno (L1) e escola (L2):

In [5]:
df.columns.map(lambda x: x[:2]).value_counts()

L2    30
L1    11
dtype: int64

In [6]:
var_alunos = [i for i in df.columns if i.startswith('L1')]
var_escolas = [i for i in df.columns if i.startswith('L2') and not 'EQUIP' in i]
var_escolas

['L2_CO_ENTIDADE',
 'L2_IN_MUNICIPIO_RIO',
 'L2_IN_MUNICIPIO_MET',
 'L2_IN_MUNICIPIO_OUT',
 'L2_IN_AGUA_CACIMBA',
 'L2_IN_LABORATORIO_CIENCIAS',
 'L2_IN_QUADRA_ESPORTES_DESCOBERTA',
 'L2_IN_BANHEIRO_FORA_PREDIO',
 'L2_IN_AUDITORIO',
 'L2_IN_ALOJAM_ALUNO',
 'L2_NU_COMP_ALUNO',
 'L2_NU_FUNCIONARIOS',
 'L2_IN_EJA',
 'L2_IN_COMUM_FUND_AF',
 'L2_NU_INSE_VALOR',
 'L2_IN_COMUNIDADE_1KM',
 'L2_IN_COMUNIDADE_5KM',
 'L2_IN_TIROTEIO_1KM',
 'L2_IN_TIROTEIO_5KM']

In [7]:
var_escolas.remove('L2_IN_AGUA_CACIMBA')
len(var_escolas)

18

In [8]:
df = df[var_alunos+var_escolas]
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 146214 entries, 112132289130 to 112980381895
Data columns (total 29 columns):
L1_NU_IDADE_REFERENCIA              146214 non-null int64
L1_IN_SEXO                          146214 non-null int64
L1_TP_COR_RACA                      146214 non-null int64
L1_IN_TRANSPORTE_PUBLICO            146214 non-null int64
L1_ID_TURMA                         146214 non-null int64
L1_IN_EVASAO                        146214 non-null int64
L1_IN_DISTORCAO                     146214 non-null int64
L1_IN_MUNICIPIO_NASC_RIO            146214 non-null int64
L1_IN_MUNICIPIO_NASC_MET            146214 non-null int64
L1_IN_MUNICIPIO_NASC_OUT            146214 non-null int64
L1_IN_DIF_MUN_ESCOLA_NASC           146214 non-null int64
L2_CO_ENTIDADE                      146214 non-null int64
L2_IN_MUNICIPIO_RIO                 146214 non-null int64
L2_IN_MUNICIPIO_MET                 146214 non-null int64
L2_IN_MUNICIPIO_OUT                 146214 non-null int64
L2

## Separação treino-teste

- 70/30% para treino/teste

In [9]:
X = df.drop('L1_IN_EVASAO', axis=1)
X.head(2)

L1_NU_IDADE_REFERENCIA  L1_IN_SEXO  L1_TP_COR_RACA  \
L1_ID                                                              
112132289130                      16           1               0   
113220290328                      20           1               0   

              L1_IN_TRANSPORTE_PUBLICO  L1_ID_TURMA  L1_IN_DISTORCAO  \
L1_ID                                                                  
112132289130                         0      6062013                0   
113220290328                         0      6062013                1   

              L1_IN_MUNICIPIO_NASC_RIO  L1_IN_MUNICIPIO_NASC_MET  \
L1_ID                                                              
112132289130                         0                         0   
113220290328                         0                         0   

              L1_IN_MUNICIPIO_NASC_OUT  L1_IN_DIF_MUN_ESCOLA_NASC  \
L1_ID                                                               
112132289130                         1                          0   
113220290328                         1                          0   

              L2_CO_ENTIDADE  L2_IN_MUNICIPIO_RIO  L2_IN_MUNICIPIO_MET  \
L1_ID                                                                    
112132289130        33009627                    0                    0   
113220290328        33009627                    0                    0   

              L2_IN_MUNICIPIO_OUT  L2_IN_LABORATORIO_CIENCIAS  \
L1_ID                                                           
112132289130                    1                         1.0   
113220290328                    1                         1.0   

              L2_IN_QUADRA_ESPORTES_DESCOBERTA  L2_IN_BANHEIRO_FORA_PREDIO  \
L1_ID                                                                        
112132289130                               0.0                         1.0   
113220290328                               0.0                         1.0   

              L2_IN_AUDITORIO  L2_IN_ALOJAM_ALUNO  L2_NU_COMP_ALUNO  \
L1_ID                                                                 
112132289130              1.0                 0.0              72.0   
113220290328              1.0                 0.0              72.0   

              L2_NU_FUNCIONARIOS  L2_IN_EJA  L2_IN_COMUM_FUND_AF  \
L1_ID                                                              
112132289130               228.0        0.0                  0.0   
113220290328               228.0        0.0                  0.0   

              L2_NU_INSE_VALOR  L2_IN_COMUNIDADE_1KM  L2_IN_COMUNIDADE_5KM  \
L1_ID                                                                        
112132289130             48.78                   1.0                   1.0   
113220290328             48.78                   1.0                   1.0   

              L2_IN_TIROTEIO_1KM  L2_IN_TIROTEIO_5KM  
L1_ID                                                 
112132289130                 0.0                 0.0  
113220290328                 0.0                 0.0

In [10]:
y = df['L1_IN_EVASAO']
y.head(2)

L1_ID
112132289130    0
113220290328    1
Name: L1_IN_EVASAO, dtype: int64

### Estratificada

In [11]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=0, 
                                                    stratify=X['L2_CO_ENTIDADE'])

In [12]:
len(X_train['L2_CO_ENTIDADE'].unique()) == len(X_test['L2_CO_ENTIDADE'].unique()) 

True

In [13]:
y_train.value_counts(normalize=True)

0    0.683417
1    0.316583
Name: L1_IN_EVASAO, dtype: float64

In [14]:
y_test.value_counts(normalize=True)

0    0.682731
1    0.317269
Name: L1_IN_EVASAO, dtype: float64

### Aleatória (balanceada)

In [15]:
# from sklearn.model_selection import train_test_split
# X_train_ran, X_test_rand, y_train_ran, y_test_rand = train_test_split(X, y, test_size=0.3, random_state=0)

## Nomalizando variáveis de aluno

- 8 variáveis de aluno

In [19]:
aluno = [i for i in X_train.columns if i.startswith('L1')]
aluno

['L1_NU_IDADE_REFERENCIA',
 'L1_IN_SEXO',
 'L1_TP_COR_RACA',
 'L1_IN_TRANSPORTE_PUBLICO',
 'L1_ID_TURMA',
 'L1_IN_DISTORCAO',
 'L1_IN_MUNICIPIO_NASC_RIO',
 'L1_IN_MUNICIPIO_NASC_MET',
 'L1_IN_MUNICIPIO_NASC_OUT',
 'L1_IN_DIF_MUN_ESCOLA_NASC']

In [20]:
X_aluno = X_train[aluno].copy()     
X_aluno.head(2)

L1_NU_IDADE_REFERENCIA  L1_IN_SEXO  L1_TP_COR_RACA  \
L1_ID                                                              
114141823685                      16           0               3   
111620175702                      15           0               2   

              L1_IN_TRANSPORTE_PUBLICO  L1_ID_TURMA  L1_IN_DISTORCAO  \
L1_ID                                                                  
114141823685                         0      8282560                0   
111620175702                         1      8272713                0   

              L1_IN_MUNICIPIO_NASC_RIO  L1_IN_MUNICIPIO_NASC_MET  \
L1_ID                                                              
114141823685                         1                         0   
111620175702                         1                         0   

              L1_IN_MUNICIPIO_NASC_OUT  L1_IN_DIF_MUN_ESCOLA_NASC  
L1_ID                                                              
114141823685                         0                          0  
111620175702                         0                          1

In [21]:
pd.Series(aluno).apply(lambda x: x[:5]).value_counts()

L1_IN    7
L1_NU    1
L1_ID    1
L1_TP    1
dtype: int64

In [22]:
indicadoras = [i for i in aluno if i.startswith('L1_IN')]
X_aluno_norm = X_aluno[indicadoras]

### Normalizando idade: MixMax

In [23]:
X_aluno['L1_NU_IDADE_REFERENCIA'].iplot(kind='hist', color=colorscale[0], 
                                 title='Distribuição da idade por aluno')

In [24]:
mu = X_aluno['L1_NU_IDADE_REFERENCIA'].mean()
std = X_aluno['L1_NU_IDADE_REFERENCIA'].std()

def normalize_idade(x):
    return (x - mu) / (std**2)

# xmin = X_aluno['L1_NU_IDADE_REFERENCIA'].min()
# xmax = X_aluno['L1_NU_IDADE_REFERENCIA'].max()

# def normalize_idade(x):
    
#     return (x - xmin) / (xmax - xmin)

X_aluno_norm['L1_NU_IDADE_REFERENCIA'] = X_aluno['L1_NU_IDADE_REFERENCIA']
X_aluno_norm['L1_NU_IDADE_REFERENCIA_NORM'] = X_aluno['L1_NU_IDADE_REFERENCIA'].apply(normalize_idade)

In [25]:
X_aluno_norm['L1_NU_IDADE_REFERENCIA_NORM'].describe()

count    1.023490e+05
mean     5.088049e-16
std      8.203980e-01
min     -3.376726e+00
25%     -6.845150e-01
50%     -1.146207e-02
75%      6.615908e-01
max      3.353802e+00
Name: L1_NU_IDADE_REFERENCIA_NORM, dtype: float64

In [26]:
X_aluno_norm['L1_NU_IDADE_REFERENCIA_NORM'].iplot(kind='hist', color=colorscale[0], 
                                 title='Distribuição da idade por aluno')

## Normalizando variáveis de escola
- 39 variáveis de escola

In [27]:
escola = [i for i in X_train.columns if i.startswith('L2')]
len(escola)

18

In [28]:
X_escola = X_train[escola] \
        .drop_duplicates(subset='L2_CO_ENTIDADE') \
        .set_index('L2_CO_ENTIDADE', drop=True)
        
X_escola.head(2)

L2_IN_MUNICIPIO_RIO  L2_IN_MUNICIPIO_MET  L2_IN_MUNICIPIO_OUT  \
L2_CO_ENTIDADE                                                                  
33136424                          1                    0                    0   
33059284                          0                    1                    0   

                L2_IN_LABORATORIO_CIENCIAS  L2_IN_QUADRA_ESPORTES_DESCOBERTA  \
L2_CO_ENTIDADE                                                                 
33136424                               0.0                               1.0   
33059284                               1.0                               1.0   

                L2_IN_BANHEIRO_FORA_PREDIO  L2_IN_AUDITORIO  \
L2_CO_ENTIDADE                                                
33136424                               0.0              0.0   
33059284                               1.0              1.0   

                L2_IN_ALOJAM_ALUNO  L2_NU_COMP_ALUNO  L2_NU_FUNCIONARIOS  \
L2_CO_ENTIDADE                                                             
33136424                       0.0              10.0               103.0   
33059284                       1.0              10.0                37.0   

                L2_IN_EJA  L2_IN_COMUM_FUND_AF  L2_NU_INSE_VALOR  \
L2_CO_ENTIDADE                                                     
33136424              0.0                  0.0             48.28   
33059284              0.0                  1.0             49.77   

                L2_IN_COMUNIDADE_1KM  L2_IN_COMUNIDADE_5KM  \
L2_CO_ENTIDADE                                               
33136424                         1.0                   1.0   
33059284                         1.0                   1.0   

                L2_IN_TIROTEIO_1KM  L2_IN_TIROTEIO_5KM  
L2_CO_ENTIDADE                                          
33136424                       1.0                 1.0  
33059284                       1.0                 1.0

In [29]:
pd.Series(escola).apply(lambda x: x[:5]).value_counts()

L2_IN    14
L2_NU     3
L2_CO     1
dtype: int64

### Normalizando numéricas: Gaussiana

- Normalização do dado (Gaussiano): vale usar [MinMax](https://medium.com/@swethalakshmanan14/how-when-and-why-should-you-normalize-standardize-rescale-your-data-3f083def38ff)? 

In [30]:
numericas = [i for i in escola if i.startswith('L2_NU')]
numericas

['L2_NU_COMP_ALUNO', 'L2_NU_FUNCIONARIOS', 'L2_NU_INSE_VALOR']

In [31]:
X_escola[numericas].nunique()

L2_NU_COMP_ALUNO       46
L2_NU_FUNCIONARIOS    168
L2_NU_INSE_VALOR      534
dtype: int64

- Número de computadores por escola

In [32]:
X_escola['L2_NU_COMP_ALUNO'].apply(lambda x: np.log(x)).iplot(kind='hist', color=colorscale[0], 
                                 title='Distribuição do log do número de computadores por escola')

- Número de funcionários por escola

In [33]:
X_escola['L2_NU_FUNCIONARIOS'].apply(lambda x: np.log(x)).iplot(kind='hist', color=colorscale[0], 
                                 title='Distribuição do log do número de funcionários por escola')

- INSE (absoluto) por escola

In [34]:
X_escola['L2_NU_INSE_VALOR'].iplot(kind='hist', color=colorscale[0], 
                                 title='Distribuição do INSE (valor absoluto) por escola')

- Aplicando o scaler

In [35]:
from sklearn.preprocessing import StandardScaler

escola_scaler = StandardScaler() 

# fica pessimo!
# X_escola_norm = X_escola.copy()
# # passando para normal
# X_escola_norm['L2_NU_FUNCIONARIOS'] = X_escola_norm['L2_NU_FUNCIONARIOS'].apply(lambda x: np.log(x) if x != 0 else -1)
# X_escola_norm['L2_NU_COMP_ALUNO'] = X_escola_norm['L2_NU_COMP_ALUNO'].apply(lambda x: np.log(x) if x != 0 else -1)

# padronizando
X_escola_norm = pd.DataFrame(escola_scaler.fit_transform(X_escola[numericas]))

X_escola_norm.columns = X_escola[numericas].columns
X_escola_norm.index = X_escola.index
X_escola_norm.head()

L2_NU_COMP_ALUNO  L2_NU_FUNCIONARIOS  L2_NU_INSE_VALOR
L2_CO_ENTIDADE                                                        
33136424               -0.132681            0.511785         -0.434789
33059284               -0.132681           -0.915374          0.155235
33099073               -0.274693            0.209054          0.139396
33083592                0.364363            2.587651         -0.874337
33058610               -0.132681            0.100936         -0.252634

In [36]:
X_escola_norm.describe()

L2_NU_COMP_ALUNO  L2_NU_FUNCIONARIOS  L2_NU_INSE_VALOR
count      8.370000e+02        8.370000e+02      8.370000e+02
mean       5.093496e-17        1.188482e-16      2.631640e-15
std        1.000598e+00        1.000598e+00      1.000598e+00
min       -8.427425e-01       -1.326222e+00     -4.481801e+00
25%       -4.167054e-01       -6.126432e-01     -5.179466e-01
50%       -1.326806e-01       -2.017945e-01      5.227817e-02
75%        2.223503e-01        3.387958e-01      5.393452e-01
max        1.911000e+01        1.158307e+01      5.825804e+00

### Adicionando as indicadoras

In [37]:
indicadoras = [i for i in escola if i.startswith('L2_IN')]
X_escola[indicadoras].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 837 entries, 33136424 to 33006776
Data columns (total 14 columns):
L2_IN_MUNICIPIO_RIO                 837 non-null int64
L2_IN_MUNICIPIO_MET                 837 non-null int64
L2_IN_MUNICIPIO_OUT                 837 non-null int64
L2_IN_LABORATORIO_CIENCIAS          837 non-null float64
L2_IN_QUADRA_ESPORTES_DESCOBERTA    837 non-null float64
L2_IN_BANHEIRO_FORA_PREDIO          837 non-null float64
L2_IN_AUDITORIO                     837 non-null float64
L2_IN_ALOJAM_ALUNO                  837 non-null float64
L2_IN_EJA                           837 non-null float64
L2_IN_COMUM_FUND_AF                 837 non-null float64
L2_IN_COMUNIDADE_1KM                837 non-null float64
L2_IN_COMUNIDADE_5KM                837 non-null float64
L2_IN_TIROTEIO_1KM                  837 non-null float64
L2_IN_TIROTEIO_5KM                  837 non-null float64
dtypes: float64(11), int64(3)
memory usage: 98.1 KB


In [38]:
X_escola_norm = X_escola_norm.join(X_escola[indicadoras])
X_escola_norm.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 837 entries, 33136424 to 33006776
Data columns (total 17 columns):
L2_NU_COMP_ALUNO                    837 non-null float64
L2_NU_FUNCIONARIOS                  837 non-null float64
L2_NU_INSE_VALOR                    837 non-null float64
L2_IN_MUNICIPIO_RIO                 837 non-null int64
L2_IN_MUNICIPIO_MET                 837 non-null int64
L2_IN_MUNICIPIO_OUT                 837 non-null int64
L2_IN_LABORATORIO_CIENCIAS          837 non-null float64
L2_IN_QUADRA_ESPORTES_DESCOBERTA    837 non-null float64
L2_IN_BANHEIRO_FORA_PREDIO          837 non-null float64
L2_IN_AUDITORIO                     837 non-null float64
L2_IN_ALOJAM_ALUNO                  837 non-null float64
L2_IN_EJA                           837 non-null float64
L2_IN_COMUM_FUND_AF                 837 non-null float64
L2_IN_COMUNIDADE_1KM                837 non-null float64
L2_IN_COMUNIDADE_5KM                837 non-null float64
L2_IN_TIROTEIO_1KM                

In [39]:
X_escola_norm.describe()

L2_NU_COMP_ALUNO  L2_NU_FUNCIONARIOS  L2_NU_INSE_VALOR  \
count      8.370000e+02        8.370000e+02      8.370000e+02   
mean       5.093496e-17        1.188482e-16      2.631640e-15   
std        1.000598e+00        1.000598e+00      1.000598e+00   
min       -8.427425e-01       -1.326222e+00     -4.481801e+00   
25%       -4.167054e-01       -6.126432e-01     -5.179466e-01   
50%       -1.326806e-01       -2.017945e-01      5.227817e-02   
75%        2.223503e-01        3.387958e-01      5.393452e-01   
max        1.911000e+01        1.158307e+01      5.825804e+00   

       L2_IN_MUNICIPIO_RIO  L2_IN_MUNICIPIO_MET  L2_IN_MUNICIPIO_OUT  \
count           837.000000           837.000000           837.000000   
mean              0.111111             0.483871             0.405018   
std               0.314458             0.500039             0.491189   
min               0.000000             0.000000             0.000000   
25%               0.000000             0.000000             0.000000   
50%               0.000000             0.000000             0.000000   
75%               0.000000             1.000000             1.000000   
max               1.000000             1.000000             1.000000   

       L2_IN_LABORATORIO_CIENCIAS  L2_IN_QUADRA_ESPORTES_DESCOBERTA  \
count                  837.000000                        837.000000   
mean                     0.741935                          0.702509   
std                      0.437831                          0.457428   
min                      0.000000                          0.000000   
25%                      0.000000                          0.000000   
50%                      1.000000                          1.000000   
75%                      1.000000                          1.000000   
max                      1.000000                          1.000000   

       L2_IN_BANHEIRO_FORA_PREDIO  L2_IN_AUDITORIO  L2_IN_ALOJAM_ALUNO  \
count                  837.000000       837.000000          837.000000   
mean                     0.768220         0.793309            0.545998   
std                      0.422222         0.405174            0.498177   
min                      0.000000         0.000000            0.000000   
25%                      1.000000         1.000000            0.000000   
50%                      1.000000         1.000000            1.000000   
75%                      1.000000         1.000000            1.000000   
max                      1.000000         1.000000            1.000000   

        L2_IN_EJA  L2_IN_COMUM_FUND_AF  L2_IN_COMUNIDADE_1KM  \
count  837.000000           837.000000            837.000000   
mean     0.469534             0.704898              0.767025   
std      0.499369             0.456361              0.422979   
min      0.000000             0.000000              0.000000   
25%      0.000000             0.000000              1.000000   
50%      0.000000             1.000000              1.000000   
75%      1.000000             1.000000              1.000000   
max      1.000000             1.000000              1.000000   

       L2_IN_COMUNIDADE_5KM  L2_IN_TIROTEIO_1KM  L2_IN_TIROTEIO_5KM  
count            837.000000          837.000000          837.000000  
mean               0.767025            0.544803            0.544803  
std                0.422979            0.498286            0.498286  
min                0.000000            0.000000            0.000000  
25%                1.000000            0.000000            0.000000  
50%                1.000000            1.000000            1.000000  
75%                1.000000            1.000000            1.000000  
max                1.000000            1.000000            1.000000

In [40]:
# X_escola.index

In [41]:
# from sklearn.preprocessing import OrdinalEncoder

# enc = OrdinalEncoder()
# codigo_escola = enc.fit_transform(np.array(X_escola.index).reshape(-1, 1))

# dic_codigo_escola = dict(zip(list(enc.categories_[0]), list(codigo_escola.flat)))
# dic_codigo_escola

## Salvando *encoders*

In [42]:
mu, std

(16.017029966096395, 1.2189205676768935)

In [43]:
dic = dict()

dic['idade'] = {'mean': mu, 'std': std}
# dic['cod_escolas'] = {str(k): str(v) for k,v in dic_codigo_escola.items()}
# dic['idade'] = {'min': float(xmin), 'max': float(xmax)}

params_numericas = [{'mean': mean, 'std': std} for mean, std in zip(escola_scaler.mean_, escola_scaler.scale_)]
dic['var_escolas'] = dict(zip(numericas, params_numericas))

dic
# dic['var_escolas'] = {str(k): str(v) for k,v in dic_codigo_escola.items()}

{'idade': {'mean': 16.017029966096395, 'std': 1.2189205676768935},
 'var_escolas': {'L2_NU_COMP_ALUNO': {'mean': 11.868578255675029,
   'std': 14.08327951075055},
  'L2_NU_FUNCIONARIOS': {'mean': 79.3321385902031, 'std': 46.245742036189725},
  'L2_NU_INSE_VALOR': {'mean': 49.37798088410991, 'std': 2.5253199254823944}}}

In [44]:
import json

with open('encoders_strat.json', 'w') as fp:
    json.dump(dic, fp)

## Juntando dados normalizados do treino

* Adicionando o código da escola nos dados normalizados dos alunos

In [45]:
X_aluno_norm.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 102349 entries, 114141823685 to 111678172650
Data columns (total 9 columns):
L1_IN_SEXO                     102349 non-null int64
L1_IN_TRANSPORTE_PUBLICO       102349 non-null int64
L1_IN_DISTORCAO                102349 non-null int64
L1_IN_MUNICIPIO_NASC_RIO       102349 non-null int64
L1_IN_MUNICIPIO_NASC_MET       102349 non-null int64
L1_IN_MUNICIPIO_NASC_OUT       102349 non-null int64
L1_IN_DIF_MUN_ESCOLA_NASC      102349 non-null int64
L1_NU_IDADE_REFERENCIA         102349 non-null int64
L1_NU_IDADE_REFERENCIA_NORM    102349 non-null float64
dtypes: float64(1), int64(8)
memory usage: 7.8 MB


In [46]:
X_aluno_norm = X_aluno_norm.join(X_train[['L2_CO_ENTIDADE']])
X_aluno_norm[['L2_CO_ENTIDADE']].head()

L2_CO_ENTIDADE
L1_ID                       
114141823685        33136424
111620175702        33059284
111996053603        33099073
121758794100        33083592
119463878350        33058610

In [47]:
X_aluno_norm.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 102349 entries, 114141823685 to 111678172650
Data columns (total 10 columns):
L1_IN_SEXO                     102349 non-null int64
L1_IN_TRANSPORTE_PUBLICO       102349 non-null int64
L1_IN_DISTORCAO                102349 non-null int64
L1_IN_MUNICIPIO_NASC_RIO       102349 non-null int64
L1_IN_MUNICIPIO_NASC_MET       102349 non-null int64
L1_IN_MUNICIPIO_NASC_OUT       102349 non-null int64
L1_IN_DIF_MUN_ESCOLA_NASC      102349 non-null int64
L1_NU_IDADE_REFERENCIA         102349 non-null int64
L1_NU_IDADE_REFERENCIA_NORM    102349 non-null float64
L2_CO_ENTIDADE                 102349 non-null int64
dtypes: float64(1), int64(9)
memory usage: 13.6 MB


- Juntando com dados normalizados da escola

In [48]:
X_escola.head()

L2_IN_MUNICIPIO_RIO  L2_IN_MUNICIPIO_MET  L2_IN_MUNICIPIO_OUT  \
L2_CO_ENTIDADE                                                                  
33136424                          1                    0                    0   
33059284                          0                    1                    0   
33099073                          0                    1                    0   
33083592                          1                    0                    0   
33058610                          0                    1                    0   

                L2_IN_LABORATORIO_CIENCIAS  L2_IN_QUADRA_ESPORTES_DESCOBERTA  \
L2_CO_ENTIDADE                                                                 
33136424                               0.0                               1.0   
33059284                               1.0                               1.0   
33099073                               1.0                               1.0   
33083592                               1.0                               1.0   
33058610                               1.0                               0.0   

                L2_IN_BANHEIRO_FORA_PREDIO  L2_IN_AUDITORIO  \
L2_CO_ENTIDADE                                                
33136424                               0.0              0.0   
33059284                               1.0              1.0   
33099073                               1.0              1.0   
33083592                               1.0              1.0   
33058610                               1.0              1.0   

                L2_IN_ALOJAM_ALUNO  L2_NU_COMP_ALUNO  L2_NU_FUNCIONARIOS  \
L2_CO_ENTIDADE                                                             
33136424                       0.0              10.0               103.0   
33059284                       1.0              10.0                37.0   
33099073                       1.0               8.0                89.0   
33083592                       1.0              17.0               199.0   
33058610                       0.0              10.0                84.0   

                L2_IN_EJA  L2_IN_COMUM_FUND_AF  L2_NU_INSE_VALOR  \
L2_CO_ENTIDADE                                                     
33136424              0.0                  0.0             48.28   
33059284              0.0                  1.0             49.77   
33099073              1.0                  1.0             49.73   
33083592              0.0                  0.0             47.17   
33058610              1.0                  1.0             48.74   

                L2_IN_COMUNIDADE_1KM  L2_IN_COMUNIDADE_5KM  \
L2_CO_ENTIDADE                                               
33136424                         1.0                   1.0   
33059284                         1.0                   1.0   
33099073                         1.0                   1.0   
33083592                         1.0                   1.0   
33058610                         1.0                   1.0   

                L2_IN_TIROTEIO_1KM  L2_IN_TIROTEIO_5KM  
L2_CO_ENTIDADE                                          
33136424                       1.0                 1.0  
33059284                       1.0                 1.0  
33099073                       1.0                 1.0  
33083592                       1.0                 1.0  
33058610                       1.0                 1.0

In [49]:
X_escola_norm.head()

L2_NU_COMP_ALUNO  L2_NU_FUNCIONARIOS  L2_NU_INSE_VALOR  \
L2_CO_ENTIDADE                                                           
33136424               -0.132681            0.511785         -0.434789   
33059284               -0.132681           -0.915374          0.155235   
33099073               -0.274693            0.209054          0.139396   
33083592                0.364363            2.587651         -0.874337   
33058610               -0.132681            0.100936         -0.252634   

                L2_IN_MUNICIPIO_RIO  L2_IN_MUNICIPIO_MET  L2_IN_MUNICIPIO_OUT  \
L2_CO_ENTIDADE                                                                  
33136424                          1                    0                    0   
33059284                          0                    1                    0   
33099073                          0                    1                    0   
33083592                          1                    0                    0   
33058610                          0                    1                    0   

                L2_IN_LABORATORIO_CIENCIAS  L2_IN_QUADRA_ESPORTES_DESCOBERTA  \
L2_CO_ENTIDADE                                                                 
33136424                               0.0                               1.0   
33059284                               1.0                               1.0   
33099073                               1.0                               1.0   
33083592                               1.0                               1.0   
33058610                               1.0                               0.0   

                L2_IN_BANHEIRO_FORA_PREDIO  L2_IN_AUDITORIO  \
L2_CO_ENTIDADE                                                
33136424                               0.0              0.0   
33059284                               1.0              1.0   
33099073                               1.0              1.0   
33083592                               1.0              1.0   
33058610                               1.0              1.0   

                L2_IN_ALOJAM_ALUNO  L2_IN_EJA  L2_IN_COMUM_FUND_AF  \
L2_CO_ENTIDADE                                                       
33136424                       0.0        0.0                  0.0   
33059284                       1.0        0.0                  1.0   
33099073                       1.0        1.0                  1.0   
33083592                       1.0        0.0                  0.0   
33058610                       0.0        1.0                  1.0   

                L2_IN_COMUNIDADE_1KM  L2_IN_COMUNIDADE_5KM  \
L2_CO_ENTIDADE                                               
33136424                         1.0                   1.0   
33059284                         1.0                   1.0   
33099073                         1.0                   1.0   
33083592                         1.0                   1.0   
33058610                         1.0                   1.0   

                L2_IN_TIROTEIO_1KM  L2_IN_TIROTEIO_5KM  
L2_CO_ENTIDADE                                          
33136424                       1.0                 1.0  
33059284                       1.0                 1.0  
33099073                       1.0                 1.0  
33083592                       1.0                 1.0  
33058610                       1.0                 1.0

In [50]:
X_train_norm = X_aluno_norm.reset_index().merge(X_escola_norm.reset_index(), on='L2_CO_ENTIDADE', how='left').set_index('L1_ID')
X_train_norm.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 102349 entries, 114141823685 to 111678172650
Data columns (total 27 columns):
L1_IN_SEXO                          102349 non-null int64
L1_IN_TRANSPORTE_PUBLICO            102349 non-null int64
L1_IN_DISTORCAO                     102349 non-null int64
L1_IN_MUNICIPIO_NASC_RIO            102349 non-null int64
L1_IN_MUNICIPIO_NASC_MET            102349 non-null int64
L1_IN_MUNICIPIO_NASC_OUT            102349 non-null int64
L1_IN_DIF_MUN_ESCOLA_NASC           102349 non-null int64
L1_NU_IDADE_REFERENCIA              102349 non-null int64
L1_NU_IDADE_REFERENCIA_NORM         102349 non-null float64
L2_CO_ENTIDADE                      102349 non-null int64
L2_NU_COMP_ALUNO                    102349 non-null float64
L2_NU_FUNCIONARIOS                  102349 non-null float64
L2_NU_INSE_VALOR                    102349 non-null float64
L2_IN_MUNICIPIO_RIO                 102349 non-null int64
L2_IN_MUNICIPIO_MET                 102349 non-null 

In [51]:
# X_train_norm['L2_CO_ENTIDADE'] = X_train_norm['L2_CO_ENTIDADE'].map(dic_codigo_escola)

In [52]:
X_train_norm.describe()

L1_IN_SEXO  L1_IN_TRANSPORTE_PUBLICO  L1_IN_DISTORCAO  \
count  102349.000000             102349.000000    102349.000000   
mean        0.488388                  0.696607         0.301234   
std         0.499868                  0.459726         0.458796   
min         0.000000                  0.000000         0.000000   
25%         0.000000                  0.000000         0.000000   
50%         0.000000                  1.000000         0.000000   
75%         1.000000                  1.000000         1.000000   
max         1.000000                  1.000000         1.000000   

       L1_IN_MUNICIPIO_NASC_RIO  L1_IN_MUNICIPIO_NASC_MET  \
count             102349.000000             102349.000000   
mean                   0.362094                  0.360248   
std                    0.480608                  0.480075   
min                    0.000000                  0.000000   
25%                    0.000000                  0.000000   
50%                    0.000000                  0.000000   
75%                    1.000000                  1.000000   
max                    1.000000                  1.000000   

       L1_IN_MUNICIPIO_NASC_OUT  L1_IN_DIF_MUN_ESCOLA_NASC  \
count             102349.000000              102349.000000   
mean                   0.277658                   0.343814   
std                    0.447846                   0.474982   
min                    0.000000                   0.000000   
25%                    0.000000                   0.000000   
50%                    0.000000                   0.000000   
75%                    1.000000                   1.000000   
max                    1.000000                   1.000000   

       L1_NU_IDADE_REFERENCIA  L1_NU_IDADE_REFERENCIA_NORM  L2_CO_ENTIDADE  \
count           102349.000000                 1.023490e+05    1.023490e+05   
mean                16.017030                 5.088049e-16    3.307113e+07   
std                  1.218921                 8.203980e-01    5.661114e+04   
min                 11.000000                -3.376726e+00    3.300003e+07   
25%                 15.000000                -6.845150e-01    3.304352e+07   
50%                 16.000000                -1.146207e-02    3.305945e+07   
75%                 17.000000                 6.615908e-01    3.309253e+07   
max                 21.000000                 3.353802e+00    3.355823e+07   

       L2_NU_COMP_ALUNO  L2_NU_FUNCIONARIOS  L2_NU_INSE_VALOR  \
count     102349.000000       102349.000000     102349.000000   
mean           0.097468            0.553921         -0.026259   
std            1.072968            1.144353          0.821313   
min           -0.842743           -1.326222         -4.481801   
25%           -0.345699           -0.223418         -0.517947   
50%           -0.132681            0.338796         -0.034840   
75%            0.435369            1.117246          0.432428   
max           19.109996           11.583074          5.825804   

       L2_IN_MUNICIPIO_RIO  L2_IN_MUNICIPIO_MET  L2_IN_MUNICIPIO_OUT  \
count        102349.000000        102349.000000        102349.000000   
mean              0.289539             0.453214             0.257247   
std               0.453551             0.497809             0.437119   
min               0.000000             0.000000             0.000000   
25%               0.000000             0.000000             0.000000   
50%               0.000000             0.000000             0.000000   
75%               1.000000             1.000000             1.000000   
max               1.000000             1.000000             1.000000   

       L2_IN_LABORATORIO_CIENCIAS  L2_IN_QUADRA_ESPORTES_DESCOBERTA  \
count               102349.000000                     102349.000000   
mean                     0.788674                          0.721131   
std                      0.408251                          0.448445   
min                      0.000000                          0.000000   
25% 

In [53]:
# Salvando treino estratificado
X_train_norm.join(y_train).to_csv(TREAT_PATH / 'modelo' / 'df_train_strat.csv')

## Normalizando teste

In [54]:
# from copy import deepcopy
# X_test_norm = X_test.append(X_train_unb).copy()
X_test_norm = X_test
X_test.head()

L1_NU_IDADE_REFERENCIA  L1_IN_SEXO  L1_TP_COR_RACA  \
L1_ID                                                              
144781768767                      16           1               3   
113878999886                      17           0               0   
144794341783                      16           1               0   
121929922115                      15           1               3   
111528331540                      17           1               1   

              L1_IN_TRANSPORTE_PUBLICO  L1_ID_TURMA  L1_IN_DISTORCAO  \
L1_ID                                                                  
144781768767                         1      8258274                0   
113878999886                         1      8288016                1   
144794341783                         1      8318217                0   
121929922115                         1      8314231                0   
111528331540                         0      8258790                1   

              L1_IN_MUNICIPIO_NASC_RIO  L1_IN_MUNICIPIO_NASC_MET  \
L1_ID                                                              
144781768767                         0                         1   
113878999886                         0                         1   
144794341783                         1                         0   
121929922115                         1                         0   
111528331540                         0                         0   

              L1_IN_MUNICIPIO_NASC_OUT  L1_IN_DIF_MUN_ESCOLA_NASC  \
L1_ID                                                               
144781768767                         0                          0   
113878999886                         0                          1   
144794341783                         0                          0   
121929922115                         0                          0   
111528331540                         1                          1   

              L2_CO_ENTIDADE  L2_IN_MUNICIPIO_RIO  L2_IN_MUNICIPIO_MET  \
L1_ID                                                                    
144781768767        33092141                    0                    1   
113878999886        33097046                    0                    1   
144794341783        33067791                    1                    0   
121929922115        33065217                    1                    0   
111528331540        33061173                    0                    1   

              L2_IN_MUNICIPIO_OUT  L2_IN_LABORATORIO_CIENCIAS  \
L1_ID                                                           
144781768767                    0                         0.0   
113878999886                    0                         1.0   
144794341783                    0                         1.0   
121929922115                    0                         1.0   
111528331540                    0                         1.0   

              L2_IN_QUADRA_ESPORTES_DESCOBERTA  L2_IN_BANHEIRO_FORA_PREDIO  \
L1_ID                                                                        
144781768767                               0.0                         0.0   
113878999886                               1.0                         1.0   
144794341783                               1.0                         1.0   
121929922115                               1.0                         1.0   
111528331540                               1.0                         1.0   

              L2_IN_AUDITORIO  L2_IN_ALOJAM_ALUNO  L2_NU_COMP_ALUNO  \
L1_ID                                                                 
144781768767              1.0                 0.0              18.0   
113878999886              1.0                 0.0               0.0   
144794341783              1.0                 1.0               7.0   
121929922115              1.0                 1.0              25.0   
111528331540              1.0                 1.0              13.0   

              L2_NU_FUNCIONARIOS  L2_IN_EJA  L2_IN_

In [55]:
del X_test_norm['L1_ID_TURMA']

* Normalizando idade

In [56]:
# print(mu, std)

In [57]:
X_test_norm['L1_NU_IDADE_REFERENCIA_NORM'] = X_test_norm['L1_NU_IDADE_REFERENCIA'].apply(normalize_idade)

* Normalizando dados numéricos da escola

In [58]:
numericas = [i for i in escola if i.startswith('L2_NU')]

df_numericas = pd.DataFrame(escola_scaler.transform(X_test_norm[numericas]))

df_numericas.columns = X_test_norm[numericas].columns
df_numericas.index = X_test_norm.index
df_numericas.head()

L2_NU_COMP_ALUNO  L2_NU_FUNCIONARIOS  L2_NU_INSE_VALOR
L1_ID                                                               
144781768767          0.435369           -0.461278          0.079997
113878999886         -0.842743           -0.526149          0.475987
144794341783         -0.345699            1.787578         -0.197195
121929922115          0.932412           -0.201795         -0.343711
111528331540          0.080338            0.317172          0.646262

In [59]:
X_test_norm.update(df_numericas)

In [60]:
X_test_norm = X_test_norm[X_train_norm.columns]
X_test_norm.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 43865 entries, 144781768767 to 117458408005
Data columns (total 27 columns):
L1_IN_SEXO                          43865 non-null int64
L1_IN_TRANSPORTE_PUBLICO            43865 non-null int64
L1_IN_DISTORCAO                     43865 non-null int64
L1_IN_MUNICIPIO_NASC_RIO            43865 non-null int64
L1_IN_MUNICIPIO_NASC_MET            43865 non-null int64
L1_IN_MUNICIPIO_NASC_OUT            43865 non-null int64
L1_IN_DIF_MUN_ESCOLA_NASC           43865 non-null int64
L1_NU_IDADE_REFERENCIA              43865 non-null int64
L1_NU_IDADE_REFERENCIA_NORM         43865 non-null float64
L2_CO_ENTIDADE                      43865 non-null int64
L2_NU_COMP_ALUNO                    43865 non-null float64
L2_NU_FUNCIONARIOS                  43865 non-null float64
L2_NU_INSE_VALOR                    43865 non-null float64
L2_IN_MUNICIPIO_RIO                 43865 non-null int64
L2_IN_MUNICIPIO_MET                 43865 non-null int64
L2_IN_MUNI

In [61]:
X_test_norm.head()

L1_IN_SEXO  L1_IN_TRANSPORTE_PUBLICO  L1_IN_DISTORCAO  \
L1_ID                                                                 
144781768767           1                         1                0   
113878999886           0                         1                1   
144794341783           1                         1                0   
121929922115           1                         1                0   
111528331540           1                         0                1   

              L1_IN_MUNICIPIO_NASC_RIO  L1_IN_MUNICIPIO_NASC_MET  \
L1_ID                                                              
144781768767                         0                         1   
113878999886                         0                         1   
144794341783                         1                         0   
121929922115                         1                         0   
111528331540                         0                         0   

              L1_IN_MUNICIPIO_NASC_OUT  L1_IN_DIF_MUN_ESCOLA_NASC  \
L1_ID                                                               
144781768767                         0                          0   
113878999886                         0                          1   
144794341783                         0                          0   
121929922115                         0                          0   
111528331540                         1                          1   

              L1_NU_IDADE_REFERENCIA  L1_NU_IDADE_REFERENCIA_NORM  \
L1_ID                                                               
144781768767                      16                    -0.011462   
113878999886                      17                     0.661591   
144794341783                      16                    -0.011462   
121929922115                      15                    -0.684515   
111528331540                      17                     0.661591   

              L2_CO_ENTIDADE  L2_NU_COMP_ALUNO  L2_NU_FUNCIONARIOS  \
L1_ID                                                                
144781768767        33092141          0.435369           -0.461278   
113878999886        33097046         -0.842743           -0.526149   
144794341783        33067791         -0.345699            1.787578   
121929922115        33065217          0.932412           -0.201795   
111528331540        33061173          0.080338            0.317172   

              L2_NU_INSE_VALOR  L2_IN_MUNICIPIO_RIO  L2_IN_MUNICIPIO_MET  \
L1_ID                                                                      
144781768767          0.079997                    0                    1   
113878999886          0.475987                    0                    1   
144794341783         -0.197195                    1                    0   
121929922115         -0.343711                    1                    0   
111528331540          0.646262                    0                    1   

              L2_IN_MUNICIPIO_OUT  L2_IN_LABORATORIO_CIENCIAS  \
L1_ID                                                           
144781768767                    0                         0.0   
113878999886                    0                         1.0   
144794341783                    0                         1.0   
121929922115                    0                         1.0   
111528331540                    0                         1.0   

              L2_IN_QUADRA_ESPORTES_DESCOBERTA  L2_IN_BANHEIRO_FORA_PREDIO  \
L1_ID                                                                        
144781768767                               0.0                         0.0   
113878999886                               1.0                         1.0   
144794341783                               1.0                         1.0   
121929922115                               1.0                         1.0   
111528331540                               1.0                         1.0   

              L2_IN_AUDITORIO  L2_IN_ALOJAM_

In [62]:
X_test_norm.describe()

L1_IN_SEXO  L1_IN_TRANSPORTE_PUBLICO  L1_IN_DISTORCAO  \
count  43865.000000              43865.000000     43865.000000   
mean       0.487359                  0.695589         0.304548   
std        0.499846                  0.460163         0.460221   
min        0.000000                  0.000000         0.000000   
25%        0.000000                  0.000000         0.000000   
50%        0.000000                  1.000000         0.000000   
75%        1.000000                  1.000000         1.000000   
max        1.000000                  1.000000         1.000000   

       L1_IN_MUNICIPIO_NASC_RIO  L1_IN_MUNICIPIO_NASC_MET  \
count              43865.000000              43865.000000   
mean                   0.366397                  0.357643   
std                    0.481825                  0.479312   
min                    0.000000                  0.000000   
25%                    0.000000                  0.000000   
50%                    0.000000                  0.000000   
75%                    1.000000                  1.000000   
max                    1.000000                  1.000000   

       L1_IN_MUNICIPIO_NASC_OUT  L1_IN_DIF_MUN_ESCOLA_NASC  \
count              43865.000000               43865.000000   
mean                   0.275960                   0.344512   
std                    0.447002                   0.475214   
min                    0.000000                   0.000000   
25%                    0.000000                   0.000000   
50%                    0.000000                   0.000000   
75%                    1.000000                   1.000000   
max                    1.000000                   1.000000   

       L1_NU_IDADE_REFERENCIA  L1_NU_IDADE_REFERENCIA_NORM  L2_CO_ENTIDADE  \
count            43865.000000                 43865.000000    4.386500e+04   
mean                16.025214                     0.005508    3.307113e+07   
std                  1.225713                     0.824970    5.662816e+04   
min                 12.000000                    -2.703674    3.300003e+07   
25%                 15.000000                    -0.684515    3.304352e+07   
50%                 16.000000                    -0.011462    3.305945e+07   
75%                 17.000000                     0.661591    3.309253e+07   
max                 21.000000                     3.353802    3.355823e+07   

       L2_NU_COMP_ALUNO  L2_NU_FUNCIONARIOS  L2_NU_INSE_VALOR  \
count      43865.000000        43865.000000      43865.000000   
mean           0.097612            0.554321         -0.026246   
std            1.074283            1.144219          0.820794   
min           -0.842743           -1.326222         -4.481801   
25%           -0.345699           -0.223418         -0.517947   
50%           -0.132681            0.338796         -0.034840   
75%            0.435369            1.117246          0.432428   
max           19.109996           11.583074          5.825804   

       L2_IN_MUNICIPIO_RIO  L2_IN_MUNICIPIO_MET  L2_IN_MUNICIPIO_OUT  \
count         43865.000000         43865.000000         43865.000000   
mean              0.289525             0.453482             0.256993   
std               0.453547             0.497837             0.436981   
min               0.000000             0.000000             0.000000   
25%               0.000000             0.000000             0.000000   
50%               0.000000             0.000000             0.000000   
75%               1.000000             1.000000             1.000000   
max               1.000000             1.000000             1.000000   

       L2_IN_LABORATORIO_CIENCIAS  L2_IN_QUADRA_ESPORTES_DESCOBERTA  \
count                43865.000000                      43865.000000   
mean                     0.788784                          0.721281   
std                      0.408176                          0.448374   
min                      0.000000                          0.000000   
25%         

In [63]:
# y_test = y_test.append(y_train_unb)

In [64]:
X_aluno.columns

Index(['L1_NU_IDADE_REFERENCIA', 'L1_IN_SEXO', 'L1_TP_COR_RACA',
       'L1_IN_TRANSPORTE_PUBLICO', 'L1_ID_TURMA', 'L1_IN_DISTORCAO',
       'L1_IN_MUNICIPIO_NASC_RIO', 'L1_IN_MUNICIPIO_NASC_MET',
       'L1_IN_MUNICIPIO_NASC_OUT', 'L1_IN_DIF_MUN_ESCOLA_NASC'],
      dtype='object')

In [65]:
# Salvando treino balanceado
X_test_norm.join(y_test).to_csv(TREAT_PATH / 'modelo' / 'df_test_strat.csv')

In [66]:
len(X_test_norm) + len(X_train_norm)

146214

In [67]:
len(X_train_norm), len(X_test_norm)

(102349, 43865)

### Balanceamento

In [73]:
df_maj = X_train_norm[X_train_norm.index.isin(y_train[y_train == 0].index)]
df_min = X_train_norm[X_train_norm.index.isin(y_train[y_train == 1].index)]

print(len(df_maj), len(df_min))

69947 32402


In [75]:
df_maj_sample = df_maj.sample(n=len(df_min),random_state=0)
len(df_maj_sample['L2_CO_ENTIDADE'].unique())

836

In [76]:
X_train_bal = df_min.append(df_maj_sample)
y_train_bal = y_train[y_train.index.isin(X_train_bal.index)]

In [77]:
# Restante:
X_train_unb = df_maj[df_maj.index.isin(df_maj_sample.index) == False]
y_train_unb = y_train[y_train.index.isin(X_train_unb.index)]

In [78]:
# Salvando treino balanceado
X_train_bal.join(y_train_bal).to_csv(TREAT_PATH / 'modelo' / 'df_train_bal.csv')

In [17]:
# # Selecionando uma amostra da classe majoritária
# df_maj_sample = df_maj.sample(n=len(df_min),random_state=0)

# X_train = df_min.append(df_maj_sample)
# y_train = y_train_ran[y_train_ran.index.isin(X_train_bal.index)]

# # Restante:
# X_train_unb = df_maj[df_maj.index.isin(df_maj_sample.index) == False]
# y_train_unb = y_train_ran[y_train_ran.index.isin(X_train_unb.index)]

# # X_train_bal = pd.read_csv(TREAT_PATH / 'modelo' / 'df_treino_bal.csv', index_col='ID')
# # y_train_bal = X_train_bal['IN_EVASAO']
# # X_train_bal = X_train_bal.drop('IN_EVASAO', axis=1)

In [18]:
# len(X_train) + len(X_train_unb) == len(X_train_raw)

In [68]:
# X_train = pd.read_csv(TREAT_PATH / 'modelo' / 'df_treino_bruto.csv', index_col='ID')
# y_train = X_train['IN_EVASAO']
# X_train = X_train.drop('IN_EVASAO', axis=1)

# X_test = pd.read_csv(TREAT_PATH / 'modelo' / 'df_teste_bruto.csv', index_col='ID')
# y_test = X_test['IN_EVASAO']
# X_test = X_test.drop('IN_EVASAO', axis=1)